In [1]:
import string
import numpy as np
from PIL import Image
import os
import pandas as pd
from pickle import dump, load
import numpy as np
from collections import Counter 
from keras.applications.xception import Xception, preprocess_input
from keras_preprocessing.image import load_img, img_to_array
from keras.preprocessing.text import Tokenizer
from keras_preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from keras.layers import add
from keras.models import Model, load_model
from keras.layers import Input, Dense, LSTM, Embedding, Dropout
import pickle
import matplotlib.pyplot as plt
# small library for seeing the progress of loops.
from tqdm import tqdm_notebook as tqdm

tqdm().pandas()

C:\Users\prath\AppData\Local\Temp\ipykernel_17324\2559071088.py:22: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  tqdm().pandas()


0it [00:00, ?it/s]

In [2]:
df_images = r"Flickr8k_Dataset\Flicker8k_Dataset"
df_text = r"Flickr8k_text"
filename1 = r"Flickr8k_text\Flickr8k.token.txt"#run in start before text preprocessing

In [3]:
filename1

'Flickr8k_text\\Flickr8k.token.txt'

In [11]:

# Loading a text file into memory
def load_doc(filename):
    # Opening the file as read only
    file = open(filename, 'r')
    text = file.read()
    file.close()
    return text
# get all imgs with their captions
def all_img_captions(filename):
    file = load_doc(filename)
    captions = file.split('\n')
    descriptions ={}
    for caption in captions[:-1]:
        img, caption = caption.split('\t')
        if img[:-2] not in descriptions:
            descriptions[img[:-2]] = [ caption ]
        else:
            descriptions[img[:-2]].append(caption)
    return descriptions
#Data cleaning- lower casing, removing puntuations and words containing numbers
def cleaning_text(captions):
    table = str.maketrans('','',string.punctuation)
    for img,caps in captions.items():
        for i,img_caption in enumerate(caps):
            img_caption.replace("-"," ")
            desc = img_caption.split()
            #converts to lowercase
            desc = [word.lower() for word in desc]
            #remove punctuation from each token
            desc = [word.translate(table) for word in desc]
            #remove hanging 's and a 
            desc = [word for word in desc if(len(word)>1)]
            #remove tokens with numbers in them
            desc = [word for word in desc if(word.isalpha())]
            #convert back to string
            img_caption = ' '.join(desc)
            captions[img][i]= img_caption
    return captions
def text_vocabulary(descriptions):
    # build vocabulary of all unique words
    vocab = set()
    for key in descriptions.keys():
        [vocab.update(d.split()) for d in descriptions[key]]
    return vocab
#All descriptions in one file 
def save_descriptions(descriptions, filename):
    lines = list()
    for key, desc_list in descriptions.items():
        for desc in desc_list:
            lines.append(key + '\t' + desc )
    data = "\n".join(lines)
    file = open(filename,"w")
    file.write(data)
    file.close()
    
descriptions = all_img_captions(filename1)
print("Length of descriptions =" ,len(descriptions))
clean_descriptions = cleaning_text(descriptions)
vocabulary = text_vocabulary(clean_descriptions)
print("Length of vocabulary = ", len(vocabulary))
save_descriptions(clean_descriptions, "descriptions.txt")

Length of descriptions = 8092
Length of vocabulary =  8763


In [40]:
!pip install tensorflow-gpu
import tensorflow as tf
config = tf.compat.v1.ConfigProto()
config.gpu_options.allow_growth = True
session = tf.compat.v1.Session(config=config)

  Using cached tensorflow-gpu-2.12.0.tar.gz (2.6 kB)
  Running setup.py clean for tensorflow-gpu
Failed to build tensorflow-gpu
    Running setup.py install for tensorflow-gpu: started
    Running setup.py install for tensorflow-gpu: finished with status 'error'


  ERROR: Command errored out with exit status 1:
   command: 'C:\Users\prath\anaconda3\python.exe' -u -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'C:\\Users\\prath\\AppData\\Local\\Temp\\pip-install-q_621k6c\\tensorflow-gpu_6dde4ba6a86c4b40bc8c4241df46ce36\\setup.py'"'"'; __file__='"'"'C:\\Users\\prath\\AppData\\Local\\Temp\\pip-install-q_621k6c\\tensorflow-gpu_6dde4ba6a86c4b40bc8c4241df46ce36\\setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' bdist_wheel -d 'C:\Users\prath\AppData\Local\Temp\pip-wheel-mfordw65'
       cwd: C:\Users\prath\AppData\Local\Temp\pip-install-q_621k6c\tensorflow-gpu_6dde4ba6a86c4b40bc8c4241df46ce36\
  Complete output (17 lines):
  Traceback (most recent call last):
    File "<string>", line 1, in <module>
    File "C:\Users\prath\AppData\Local\Temp\pip-install-q_621k6c\tensorflow-gpu_6dde4ba6a86c4b40bc8c4241df46ce36\setup.py

In [39]:
import tensorflow as tf
print(tf.test.gpu_device_name())

In [35]:
from tensorflow.keras.applications.xception import Xception, preprocess_input
from PIL import Image
from tensorflow.keras.preprocessing import image
def extract_features(directory):
        model = Xception(include_top=False, pooling='avg')
        features = {}
        for img_ in tqdm(os.listdir(directory)):
            filename = directory+ "/" + img_
            img = Image.open(filename)
            img=img.resize((299,299))
            img = image.img_to_array(img)
            img = np.expand_dims(img, axis=0)
            #image = preprocess_input(image)
            img = img/127.5
            img = img - 1.0
            feature = model.predict(img)
            features[img_] = feature
        return features
# import os
# import numpy as np
# from tqdm import tqdm
# from PIL import Image
# from tensorflow.keras.applications.xception import Xception, preprocess_input
# from tensorflow.keras.preprocessing import image

# def extract_features(directory, batch_size=32):
#     model = Xception(include_top=False, pooling='avg', input_shape=(299, 299, 3))
#     features = {}
#     image_generator = image.ImageDataGenerator(preprocessing_function=preprocess_input).flow_from_directory(
#         directory,
#         target_size=(299, 299),
#         batch_size=batch_size,
#         class_mode=None,
#         shuffle=False
#     )
#     for i, batch in tqdm(enumerate(image_generator), total=np.ceil(len(image_generator.filenames) / batch_size)):
#         batch_features = model.predict(batch)
#         for j, filename in enumerate(image_generator.filenames[i * batch_size:(i + 1) * batch_size]):
#             img_id = filename.split('.')[0]
#             features[img_id] = batch_features[j]
#     return features


In [36]:
directory = r'Flickr8k_Dataset/Flicker8k_Dataset'
features=extract_features(directory)

  7%|█████▌                                                                         | 569/8091 [04:18<56:57,  2.20it/s]


KeyboardInterrupt: 

In [107]:
from os import listdir
from pickle import dump
from keras.applications.vgg16 import VGG16
from keras.preprocessing.image import load_img
from keras.preprocessing.image import img_to_array
from keras.applications.vgg16 import preprocess_input
from keras.models import Model

# extract features from each photo in the directory
def extract_features(directory):
	# load the model
	model = VGG16()
	# re-structure the model
	model = Model(inputs=model.inputs, outputs=model.layers[-2].output)
	# summarize
	print(model.summary())
	# extract features from each photo
	features = dict()
	for name in listdir(directory):
		# load an image from file
		filename = directory + '/' + name
		image = load_img(filename, target_size=(224, 224))
		# convert the image pixels to a numpy array
		image = img_to_array(image)
		# reshape data for the model
		image = image.reshape((1, image.shape[0], image.shape[1], image.shape[2]))
		# prepare the image for the VGG model
		image = preprocess_input(image)
		# get features
		feature = model.predict(image, verbose=0)
		# get image id
		image_id = name.split('.')[0]
		# store feature
		features[image_id] = feature
		print('>%s' % name)
	return features

# extract features from all images
directory = 'Flickr8k_Dataset/Flicker8k_Dataset'
features = extract_features(directory)
print('Extracted Features: %d' % len(features))
# save to file
dump(features, open('features_vgg.pkl', 'wb'))

553476096/553467096 [==============================] - 195s 0us/step
Model: "model_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_12 (InputLayer)       [(None, 224, 224, 3)]     0         
                                                                 
 block1_conv1 (Conv2D)       (None, 224, 224, 64)      1792      
                                                                 
 block1_conv2 (Conv2D)       (None, 224, 224, 64)      36928     
                                                                 
 block1_pool (MaxPooling2D)  (None, 112, 112, 64)      0         
                                                                 
 block2_conv1 (Conv2D)       (None, 112, 112, 128)     73856     
                                                                 
 block2_conv2 (Conv2D)       (None, 112, 112, 128)     147584    
                                                        

>1204996216_71d7519d9a.jpg
>1206506157_c7956accd5.jpg
>1207159468_425b902bfb.jpg
>1211015912_9f3ee3a995.jpg
>1213336750_2269b51397.jpg
>1215334959_b1970965f7.jpg
>121800200_bef08fae5f.jpg
>121971540_0a986ee176.jpg
>1220401002_3f44b1f3f7.jpg
>1222322358_225067636e.jpg
>1224851143_33bcdd299c.jpg
>1225443522_1633e7121f.jpg
>1227655020_b11a1bb112.jpg
>1229756013_94663527d7.jpg
>1231229740_8dcbf80bfb.jpg
>1232148178_4f45cc3284.jpg
>1234293791_6566284bcd.jpg
>1234817607_924893f6e1.jpg
>1235580648_7eebaed9bc.jpg
>1235681222_819231767a.jpg
>1235685934_be89b231fb.jpg
>1236951314_0308dc4138.jpg
>1236964638_1808784a3c.jpg
>1237985362_dbafc59280.jpg
>123889082_d3751e0350.jpg
>123997871_6a9ca987b1.jpg
>1240297429_c36ae0c58f.jpg
>124195430_d14028660f.jpg
>1244140539_da4804d828.jpg
>1244306891_8e78ae1620.jpg
>1244485675_822e6efe60.jpg
>1245022983_fb329886dd.jpg
>1247181182_35cabd76f3.jpg
>1248357227_2b4175fc39.jpg
>1248734482_3038218f3b.jpg
>124881487_36e668145d.jpg
>1248940539_46d33ed487.jpg
>124895

>1449692616_60507875fb.jpg
>1452361926_6d8c535e32.jpg
>1453366750_6e8cf601bf.jpg
>1454678644_7e5a371301.jpg
>1454841725_4b6e6199e2.jpg
>1456393634_74022d9056.jpg
>1456630952_dd4778a48f.jpg
>145721496_687af9bb18.jpg
>145721498_a27d2db576.jpg
>1457762320_7fe121b285.jpg
>1459032057_97e73ed6ab.jpg
>1459250022_bf1eddad11.jpg
>1460352062_d64fb633e0.jpg
>1460500597_866fa0c6f3.jpg
>146098876_0d99d7fb98.jpg
>146100443_906d87faa2.jpg
>1461329041_c623b06e5b.jpg
>1461653394_8ab96aae63.jpg
>1461667284_041c8a2475.jpg
>1463638541_c02cfa04dc.jpg
>1463732130_a754441289.jpg
>1463732807_0cdf4f22c7.jpg
>1464120327_d90279ca3a.jpg
>1465666502_de289b3b9c.jpg
>146577645_91b570c0d0.jpg
>146577646_9e64b8c2dc.jpg
>1466307485_5e6743332e.jpg
>1466307489_cb8a74de09.jpg
>1466479163_439db855af.jpg
>1467533293_a2656cc000.jpg
>1468103286_96a6e07029.jpg
>1468389504_c724bdcad0.jpg
>1468429623_f001988691.jpg
>1468962616_5803b4397f.jpg
>1469000260_5d473c8283.jpg
>1469358746_2a879abaf3.jpg
>1470061031_4cb59c12a8.jpg
>147013

>1917265421_aeccf1ca38.jpg
>1918573100_d31cbb6b77.jpg
>19212715_20476497a3.jpg
>1921398767_771743bf4e.jpg
>1923476156_e20976b32d.jpg
>1924234308_c9ddcf206d.jpg
>1925434818_2949a8f6d8.jpg
>1926129518_4350f4f552.jpg
>1928319708_ccf1f4ee72.jpg
>1931690777_897a7d8ab6.jpg
>1932161768_996eadac87.jpg
>1932314876_9cc46fd054.jpg
>1936215201_d03a75cbba.jpg
>1937104503_313d22a2d0.jpg
>1937262236_cbf5bfa101.jpg
>1947351225_288d788983.jpg
>195084264_72fb347b0f.jpg
>1952896009_cee8147c90.jpg
>1956678973_223cb1b847.jpg
>1956944011_c5661d3f22.jpg
>1957371533_62bc720bac.jpg
>195962284_e57178054a.jpg
>195962790_3380aea352.jpg
>1962729184_6996e128e7.jpg
>1965278563_8279e408de.jpg
>1969573381_5ecfae4c80.jpg
>197107117_4b438b1872.jpg
>197142902_f05ff198c2.jpg
>197504190_fd1fc3d4b7.jpg
>1975171469_84e425f61b.jpg
>1975531316_8b00eeaaf7.jpg
>1977827746_4e13d7e19f.jpg
>197924859_f6e39a7dfa.jpg
>1980315248_82dbc34676.jpg
>1980882959_9a161f3469.jpg
>1982852140_56425fa7a2.jpg
>1984936420_3f3102132b.jpg
>198914528

>214501174_6db1f4d69c.jpg
>214543992_ce6c0d9f9b.jpg
>2147199188_d2d70b88ec.jpg
>2148013097_6a4f495bc5.jpg
>2148695079_9ae6a9b1c7.jpg
>2148916767_644ea6a7fa.jpg
>2148991939_3b9fd6c439.jpg
>2149968397_a7411729d1.jpg
>2149982207_5345633bbf.jpg
>2150564996_d173a506d7.jpg
>2151056407_c9c09b0a02.jpg
>2151300603_248a9fe715.jpg
>215214751_e913b6ff09.jpg
>2156131463_5b53636cf0.jpg
>2156726763_034ecd2e39.jpg
>2157003092_eaeb977789.jpg
>2157173498_2eea42ee38.jpg
>2158247955_484f0a1f11.jpg
>2158267555_db1d94e468.jpg
>215876547_fa584c5ec3.jpg
>2159447283_fab8c272b0.jpg
>2160266952_a2ab39191b.jpg
>216172386_9ac5356dae.jpg
>2161799386_27aa938421.jpg
>2162469360_ff777edc95.jpg
>2162564553_96de62c7e6.jpg
>2164363131_6930455d45.jpg
>2165459064_5b81ff23eb.jpg
>2165461920_1a4144eb2b.jpg
>2165677531_e1d5e086f7.jpg
>2167644298_100ca79f54.jpg
>2169067981_cc19268f23.jpg
>2169951750_495820a215.jpg
>2170187328_65c2f11891.jpg
>2170222061_e8bce4a32d.jpg
>2171154778_8189169336.jpg
>2171576939_d1e72daab2.jpg
>21718

...

>3623302162_099f983d58.jpg
>3623331945_df0f51d7dd.jpg
>3623650392_7b75d4de21.jpg
>3624076529_9793655a21.jpg
>3624327440_bef4f33f32.jpg
>3624676866_8f6d0efcc9.jpg
>3625049113_554d82c2a1.jpg
>3625519177_4c2bb9e7f0.jpg
>3625957413_e475943aa3.jpg
>3626475209_f71cdd06bd.jpg
>3626642428_3396568c3c.jpg
>3626689571_5817f99c0e.jpg
>3626964430_cb5c7e5acc.jpg
>3626998066_3ae11ee278.jpg
>3627011534_485f667b10.jpg
>3627076769_3b71e73018.jpg
>3627216820_4952bacbcb.jpg
>3627290893_561e176e80.jpg
>3627676364_1dc9294ec5.jpg
>3627679667_0e3de9fc90.jpg
>3628017876_4ac27e687b.jpg
>3628043835_9d9bd595a7.jpg
>3628059004_5c3529b120.jpg
>3628103548_2708abcda2.jpg
>3628698119_5566769777.jpg
>3628994466_a12065d29b.jpg
>3629492654_619d7b67ee.jpg
>3629664676_36bcefe6b7.jpg
>3630102841_b4c3e00b2c.jpg
>3630332976_fdba22c50b.jpg
>3630641436_8f9ac5b9b2.jpg
>3630991662_990f397f7c.jpg
>3631023049_8a85bab19f.jpg
>3631136463_53ff624b82.jpg
>3631344685_ed0f3e091b.jpg
>3631474374_e40764d153.jpg
>3631671718_d712821757.jpg
>

>3689727848_b53f931130.jpg
>3689975998_72f50b6d91.jpg
>3690107455_0fdb4ecee7.jpg
>3690159129_93ba49ea18.jpg
>3690189273_927d42ff43.jpg
>3690348036_a01f243fb0.jpg
>3690425778_3b390b3ea5.jpg
>3690431163_1d81e19549.jpg
>369047365_35476becc9.jpg
>3690883532_d883f34617.jpg
>3691592651_6e4e7f1da9.jpg
>3691622437_f13644273c.jpg
>3691670743_0ed111bcf3.jpg
>3691729694_2b97f14c1e.jpg
>3691800116_6a7b315e46.jpg
>369186134_5eef374112.jpg
>369244499_752f0c1018.jpg
>3692593096_fbaea67476.jpg
>3692746368_ab7d97ab31.jpg
>3692836015_d11180727b.jpg
>3692892751_f6574e2700.jpg
>3693297007_94512e861e.jpg
>369360998_ba56fb436f.jpg
>3693961165_9d6c333d5b.jpg
>3694064560_467683205b.jpg
>3694071771_ce760db4c7.jpg
>3694093650_547259731e.jpg
>3694219419_a7a83d4886.jpg
>3694555931_7807db2fb4.jpg
>3694991841_141804da1f.jpg
>3695064885_a6922f06b2.jpg
>3695517194_2a6b604cb2.jpg
>3695949492_27ca3892fd.jpg
>3696246123_99d4d10140.jpg
>3696698390_989f1488e7.jpg
>3697003897_d8ac13be9a.jpg
>3697153626_90fb177731.jpg
>3697

>409327234_7b29eecb4e.jpg
>410042380_517ccee020.jpg
>410413536_11f1127c46.jpg
>410422753_de506155fa.jpg
>410453140_5401bf659a.jpg
>411011549_1298d2b4d2.jpg
>411175971_0fffd3b8c6.jpg
>411216802_aead9e67e3.jpg
>411863595_d77156687e.jpg
>412056525_191724b058.jpg
>412082368_371df946b3.jpg
>412101267_7257e6d8c0.jpg
>412203580_2c7278909c.jpg
>413231421_43833a11f5.jpg
>413737417_b0a8b445e9.jpg
>414568315_5adcfc23c0.jpg
>414773731_c3f5bf43d5.jpg
>415118186_64defc96f3.jpg
>415657941_454d370721.jpg
>415793623_6c1225ae27.jpg
>416106657_cab2a107a5.jpg
>416650559_cd08d3cd96.jpg
>416788726_5b4eb1466e.jpg
>416960865_048fd3f294.jpg
>416992999_654a99a903.jpg
>417577408_eb571658c1.jpg
>417966898_a04f9b5349.jpg
>418357172_bdddf71d32.jpg
>418616992_22090c6195.jpg
>418667611_b9995000f4.jpg
>418796494_bdb441de42.jpg
>419116771_642800891d.jpg
>41999070_838089137e.jpg
>420355149_f2076770df.jpg
>421153376_d1d325568f.jpg
>421316045_ae7a1eb4bc.jpg
>421322723_3470543368.jpg
>421706022_1ddb6a7a78.jpg
>421730441_6b

>495054019_3dee8a02f5.jpg
>495055747_a75872762a.jpg
>495116214_f1df479fb0.jpg
>495340319_705f2e63d6.jpg
>495341977_b27279f962.jpg
>49553964_cee950f3ba.jpg
>496110746_a93ca191ae.jpg
>496129405_b9feeda1ab.jpg
>496380034_d22aeeedb3.jpg
>496555371_3e1ee0d97d.jpg
>496606439_9333831e73.jpg
>496971341_22782195f0.jpg
>497122685_a51b29dc46.jpg
>497579819_f91b26f7d3.jpg
>497791037_93499238d8.jpg
>498404951_527adba7b8.jpg
>498444334_a680d318a1.jpg
>498492764_fe276e505a.jpg
>498748832_941faaaf40.jpg
>498794783_cc2ac62b47.jpg
>498957941_f0eda42787.jpg
>50030244_02cd4de372.jpg
>500308355_f0c19067c0.jpg
>500446858_125702b296.jpg
>500678178_26ce0f4417.jpg
>501320769_31eea7b7ea.jpg
>501520507_c86f805ab8.jpg
>501650847_b0beba926c.jpg
>501684722_0f20c4e704.jpg
>501699433_f8df386cf9.jpg
>502115726_927dd684d3.jpg
>502671104_b2114246c7.jpg
>502783522_3656f27014.jpg
>502884177_25939ac000.jpg
>503090187_8758ab5680.jpg
>503717911_fc43cb3cf9.jpg
>503794526_603a7954d3.jpg
>504385521_6e668691a3.jpg
>504765160_b4b

>652542470_60e858da64.jpg
>654130822_4aeb1f1273.jpg
>656260720_a7db4ce48b.jpg
>661546153_9d30db6984.jpg
>661749711_6f408dad62.jpg
>661755629_602ea4cf09.jpg
>661757041_61e131e913.jpg
>662606040_8cc8cd9f1b.jpg
>664341930_bd5c8b60ea.jpg
>664470170_6a1ad20c45.jpg
>667626_18933d713e.jpg
>670609997_5c7fdb3f0b.jpg
>673806038_0a3682a83f.jpg
>684255145_db3f8e3e46.jpg
>684375286_09cc1aa778.jpg
>687513087_413d4a3a3b.jpg
>688210930_85c5675d5b.jpg
>688940111_325a74674a.jpg
>689359034_4a64c24ca4.jpg
>689776124_07f560a920.jpg
>691770760_48ce80a674.jpg
>69189650_6687da7280.jpg
>693164706_9624582e69.jpg
>693450725_8ad72389e6.jpg
>693785581_68bec8312a.jpg
>694496803_f2a05869cf.jpg
>696663662_232edd58af.jpg
>69710411_2cf537f61f.jpg
>69710415_5c2bfb1058.jpg
>697490420_67d8d2a859.jpg
>697582336_601462e052.jpg
>697778778_b52090709d.jpg
>698107542_3aa0ba78b4.jpg
>700884207_d3ec546494.jpg
>701816897_221bbe761a.jpg
>707941195_4386109029.jpg
>707972553_36816e53a2.jpg
>708860480_1a956ae0f7.jpg
>708945669_08e7ffb

In [19]:
import keras_preprocessing.image as image

In [20]:
# from keras.applications.resnet import ResNet50, preprocess_input, decode_predictions


# import numpy as np

# def extract_features_resnet50(directory):
#         model = ResNet50(include_top=False, pooling='avg')
#         features = {}
#         for img_ in tqdm(os.listdir(directory)):
#             filename = directory + "/" + img_
#             img = Image.open(filename)
#             img= image.img_to_array(img)
#             img = img.resize((224,224))
#             img = np.expand_dims(img, axis=0)
#             #image = preprocess_input(image)
#             img = img/127.5
#             img = img - 1.0
#             feature = model.predict(img)
#             features[img_] = feature
#         return features


In [21]:
# features = load(open(r"features.p","rb"))

In [22]:
# load doc into memory
def load_doc(filename):
	# open the file as read only
	file = open(filename, 'r')
	# read all text
	text = file.read()
	# close the file
	file.close()
	return text

# load a pre-defined list of photo identifiers
def load_set(filename):
	doc = load_doc(filename)
	dataset = list()
	# process line by line
	for line in doc.split('\n'):
		# skip empty lines
		if len(line) < 1:
			continue
		# get the image identifier
		identifier = line.split('.')[0]
		dataset.append(identifier)
	return set(dataset)

# load clean descriptions into memory
def load_clean_descriptions(filename, dataset):
	# load document
	doc = load_doc(filename)
	descriptions = dict()
	for line in doc.split('\n'):
		# split line by white space
		tokens = line.split()
		# split id from description
		image_id, image_desc = tokens[0], tokens[1:]
		# skip images not in the set
		if image_id in dataset:
			# create list
			if image_id not in descriptions:
				descriptions[image_id] = list()
			# wrap description in tokens
			desc = '<start> ' + ' '.join(image_desc) + ' <end>'
			# store
			descriptions[image_id].append(desc)
	return descriptions

In [23]:
# load photo features
def load_photo_features(filename, dataset):
	# load all features
	all_features = load(open(filename, 'rb'))
	# filter features
	features = {k: all_features[k] for k in dataset}
	return features

In [24]:
features_vgg=load(open(r"features_vgg.pkl","rb"))

In [32]:
filename = 'Flickr8k_text/Flickr_8k.trainImages.txt'
train = load_set(filename)
print('Dataset: %d' % len(train))
# descriptions
train_descriptions = load_clean_descriptions('descriptions.txt', train)
print('Descriptions: train=%d' % len(train_descriptions))
# photo features
train_features = load_photo_features('features_vgg.pkl', train)
print('Photos: train=%d' % len(train_features))

Dataset: 6000
Descriptions: train=6000
Photos: train=6000


In [34]:
train_descriptions

{'1000268201_693b08cb0e': ['<start> child in pink dress is climbing up set of stairs in an entry way <end>',
  '<start> girl going into wooden building <end>',
  '<start> little girl climbing into wooden playhouse <end>',
  '<start> little girl climbing the stairs to her playhouse <end>',
  '<start> little girl in pink dress going into wooden cabin <end>'],
 '1001773457_577c3a7d70': ['<start> black dog and spotted dog are fighting <end>',
  '<start> black dog and tricolored dog playing with each other on the road <end>',
  '<start> black dog and white dog with brown spots are staring at each other in the street <end>',
  '<start> two dogs of different breeds looking at each other on the road <end>',
  '<start> two dogs on pavement moving toward each other <end>'],
 '1002674143_1b742ab4b8': ['<start> little girl covered in paint sits in front of painted rainbow with her hands in bowl <end>',
  '<start> little girl is sitting in front of large painted rainbow <end>',
  '<start> small gir

In [26]:
# filename = df_text + "\\" + "Flickr_8k.trainImages.txt"
# train_images=load_photos(filename)

# def load_photos(filename):
#     file = load_doc(filename)
#     images = file.split("\n")[:-1]
#     return images
# filename1 = df_text + "\\" + "Flickr_8k.testImages.txt"
# test_images=load_photos(filename)
# test_desc=load_clean("descriptions.txt", test_images)
# test_features=load_features(test_images)

In [27]:
##train_desc=load_clean("descriptions.txt", train_images)

In [28]:
# def load_features(images):
#     ##features = load(open(r"C:\Users\hp\Desktop\Random_Programs\Python\projects\venv\Actual_projects\Image_Caption_Generator\features.p","rb"))
#     features = load(open(r"features.p","rb"))
#     selected_features = {i:features[i] for i in images}
#     return selected_features

In [29]:
#train_features = load_features(train_images)

In [30]:
#tokenizing

In [37]:
train_descriptions

{'1000268201_693b08cb0e': ['<start> child in pink dress is climbing up set of stairs in an entry way <end>',
  '<start> girl going into wooden building <end>',
  '<start> little girl climbing into wooden playhouse <end>',
  '<start> little girl climbing the stairs to her playhouse <end>',
  '<start> little girl in pink dress going into wooden cabin <end>'],
 '1001773457_577c3a7d70': ['<start> black dog and spotted dog are fighting <end>',
  '<start> black dog and tricolored dog playing with each other on the road <end>',
  '<start> black dog and white dog with brown spots are staring at each other in the street <end>',
  '<start> two dogs of different breeds looking at each other on the road <end>',
  '<start> two dogs on pavement moving toward each other <end>'],
 '1002674143_1b742ab4b8': ['<start> little girl covered in paint sits in front of painted rainbow with her hands in bowl <end>',
  '<start> little girl is sitting in front of large painted rainbow <end>',
  '<start> small gir

In [38]:
from keras.preprocessing.text import Tokenizer
def create_tokenizer(descriptions):
    all_desc = list()
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(all_desc)
    return tokenizer
# prepare tokenizer
tokenizer = create_tokenizer(train_descriptions)
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)


Vocabulary Size: 7577


In [39]:
dump(tokenizer, open('tokenizer_vgg.pkl', 'wb'))

In [40]:
def max_length(descriptions):
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return max(len(d.split()) for d in all_desc)
    
max_length = max_length(descriptions)
max_length

32

In [41]:
vocab_size

7577

In [42]:
def data_generator(descriptions, features, tokenizer, max_length,vocab_size):
    
    while 1:
        for key, description_list in list(descriptions.items())[:1]:
            #retrieve photo features
            feature = features[key][0]
            print(features)
            input_image, input_sequence, output_word = create_sequences(tokenizer, max_length, description_list, feature,vocab_size)
            yield [[input_image, input_sequence], output_word]
def create_sequences(tokenizer, max_length, desc_list, feature,vocab_size):
    X1, X2, y = list(), list(), list()
    # walk through each description for the image
    for desc in desc_list:
        # encode the sequence
        seq = tokenizer.texts_to_sequences([desc])[0]
        # split one sequence into multiple X,y pairs
        for i in range(1, len(seq)):
            # split into input and output pair
            in_seq, out_seq = seq[:i], seq[i]
            # pad input sequence
            in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
            # encode output sequence
            out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
            # store
            X1.append(feature)
            X2.append(in_seq)
            y.append(out_seq)
            #print(np.array(X1))
    return np.array(X1), np.array(X2), np.array(y)


In [43]:
[a,b],c=next(data_generator(train_descriptions, features_vgg, tokenizer, max_length,vocab_size))

{'1000268201_693b08cb0e': array([[2.5076485, 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ]], dtype=float32), '1001773457_577c3a7d70': array([[0.       , 0.       , 0.4941072, ..., 0.       , 0.       ,
        0.       ]], dtype=float32), '1002674143_1b742ab4b8': array([[1.4937081, 0.       , 0.5356844, ..., 2.3154147, 3.741841 ,
        0.       ]], dtype=float32), '1003163366_44323f5815': array([[0., 0., 0., ..., 0., 0., 0.]], dtype=float32), '1007129816_e794419615': array([[0.        , 0.09227607, 0.        , ..., 0.        , 0.        ,
        0.06529289]], dtype=float32), '1007320043_627395c3d8': array([[0.      , 0.      , 0.      , ..., 0.      , 3.338643, 0.      ]],
      dtype=float32), '1009434119_febe49276a': array([[2.0962942, 2.1193209, 3.5624356, ..., 0.6426416, 2.7146513,
        0.       ]], dtype=float32), '1012212859_01547e3f17': array([[0.        , 0.        , 0.9873719 , ..., 0.        , 1.4932487 ,
        0.86128545]], dtype=float32), '1015

In [44]:
a.shape ,b.shape ,c.shape

((47, 4096), (47, 32), (47, 7577))

In [52]:
from keras.layers import GRU
from keras.models import Model

In [53]:
# define the captioning model
from keras.utils.vis_utils import plot_model
def define_model(vocab_size, max_length):
    
    # features from the CNN model squeezed from 2048 to 256 nodes
    inputs1 = Input(shape=(4096,))
    fe1 = Dropout(0.5)(inputs1)
    fe2 = Dense(256, activation='relu')(fe1)
    
    
    # gru sequence model
    inputs2 = Input(shape=(max_length,))
    se1 = Embedding(vocab_size, 256, mask_zero=True)(inputs2)
    se2 = Dropout(0.5)(se1)
    se3 = GRU(units=256)(se2)
    
    
    # Merging both models
    decoder1 = add([fe2, se3])
    decoder2 = Dense(256, activation='relu')(decoder1)
    outputs = Dense(vocab_size, activation='softmax')(decoder2)
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam')
 

    print(model.summary())
    plot_model(model, to_file='model.png', show_shapes=True)
    return model

In [47]:
!pip install pydot

In [48]:
# load test set
filename = 'Flickr8k_text/Flickr_8k.devImages.txt'
test = load_set(filename)
print('Dataset: %d' % len(test))
# descriptions
test_descriptions = load_clean_descriptions('descriptions.txt', test)
print('Descriptions: test=%d' % len(test_descriptions))
# photo features
test_features = load_photo_features('features_vgg.pkl', test)
print('Photos: test=%d' % len(test_features))
# prepare sequences

Dataset: 1000
Descriptions: test=1000
Photos: test=1000


In [49]:
[d,e],f=next(data_generator(test_descriptions, test_features, tokenizer, max_length,vocab_size))

{'2908466042_bf07cb52c7': array([[0.        , 0.        , 1.0885444 , ..., 0.        , 2.0711055 ,
        0.19850162]], dtype=float32), '3257182199_5fda78d870': array([[0.       , 0.       , 1.1721687, ..., 0.       , 2.769802 ,
        0.       ]], dtype=float32), '2647062476_5ef31ba867': array([[0.4609664, 2.3048491, 0.5132934, ..., 0.       , 3.1796415,
        2.817108 ]], dtype=float32), '3444684583_6656e38088': array([[1.6886336 , 0.18278101, 5.359283  , ..., 0.        , 0.        ,
        0.        ]], dtype=float32), '1468389504_c724bdcad0': array([[1.6263016, 0.       , 0.       , ..., 0.       , 1.4139264,
        0.       ]], dtype=float32), '241347664_4a3e7e5be7': array([[1.0515242 , 0.        , 0.33542255, ..., 0.        , 0.        ,
        0.5142932 ]], dtype=float32), '3405011838_f81117c99f': array([[2.230611 , 0.       , 0.       , ..., 0.       , 1.8594625,
        0.       ]], dtype=float32), '2307451605_22e9c06530': array([[0.       , 0.       , 0.       , ..., 0

In [ ]:
# train the model, run epochs manually and save after each epoch
epochs = 10
steps = len(train_descriptions)
model=define_model(vocab_size,max_length)
os.mkdir('models2')
for i in range(epochs):
 # create the data generator
    generator = data_generator(train_descriptions, train_features, tokenizer, max_length, vocab_size)
 # fit for one epoch
    history=model.fit_generator(generator, epochs=1, steps_per_epoch=steps,verbose=1)
    train_loss += history.history['loss']
    train_accuracy += history.history['accuracy']
    model.save('models2/model_' + str(i) + '.h5')

# plot the training loss
plt.plot(train_loss)
plt.title('Training Loss')
plt.ylabel('Loss')
plt.xlabel('Epoch')
plt.savefig('train_loss.png')

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_2 (InputLayer)           [(None, 32)]         0           []                               
                                                                                                  
 input_1 (InputLayer)           [(None, 4096)]       0           []                               
                                                                                                  
 embedding (Embedding)          (None, 32, 256)      1939712     ['input_2[0][0]']                
                                                                                                  
 dropout (Dropout)              (None, 4096)         0           ['input_1[0][0]']                
                                                                                              

C:\Users\prath\AppData\Local\Temp\ipykernel_10552\2410896281.py:10: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  history=model.fit_generator(generator, epochs=1, steps_per_epoch=steps,verbose=1)


{'244910130_e1f823a28a': array([[1.179996 , 2.0402312, 0.       , ..., 0.       , 1.0499623,
        0.7331567]], dtype=float32), '2797185895_4d9e1e9508': array([[0.42599994, 0.        , 0.        , ..., 1.0045527 , 0.29467225,
        1.0929022 ]], dtype=float32), '3621652774_fd9634bd5b': array([[0.       , 0.       , 1.2267206, ..., 0.       , 0.       ,
        2.2394056]], dtype=float32), '3204686006_88f04547b9': array([[2.5601568, 0.       , 0.8621752, ..., 0.       , 4.486675 ,
        0.5409367]], dtype=float32), '310213587_778fe8fb5b': array([[0.94904435, 2.0886014 , 0.        , ..., 0.        , 0.6676428 ,
        0.        ]], dtype=float32), '2091171488_c8512fec76': array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.94063747]], dtype=float32), '232193739_ed5f348c7a': array([[1.8454651 , 0.        , 0.67651856, ..., 0.5742634 , 0.        ,
        1.6031334 ]], dtype=float32), '2562377955_8d670ccec6': array([[0.       , 4.2445645, 5.359257 , ..

In [68]:
# map an integer to a word
def word_for_id(integer, tokenizer):
	for word, index in tokenizer.word_index.items():
		if index == integer:
			return word
	return None

# generate a description for an image
def generate_desc(model, tokenizer, photo, max_length):
	# seed the generation process
	in_text = '<start>'
	# iterate over the whole length of the sequence
	for i in range(max_length):
		# integer encode input sequence
		sequence = tokenizer.texts_to_sequences([in_text])[0]
		# pad input
		sequence = pad_sequences([sequence], maxlen=max_length)
		# predict next word
		yhat = model.predict([photo,sequence], verbose=0)
		# convert probability to integer
		yhat = argmax(yhat)
		# map integer to word
		word = word_for_id(yhat, tokenizer)
		# stop if we cannot map the word
		if word is None:
			break
		# append as input for generating the next word
		in_text += ' ' + word
		# stop if we predict the end of the sequence
		if word == '<end>':
			break
	return in_text

In [79]:
for img_id, img_features in list(test_features.items())[:1]:
    print("Image ID:", img_id)
    print("Image features shape:", img_features)

Image ID: 2513260012_03d33305cf.jpg
Image features shape: [[0.         0.13564937 0.         ... 0.33939147 0.         0.03670813]]


In [103]:
# evaluate the skill of the model
def evaluate_model(model, descriptions, photos, tokenizer, max_length):
	actual, predicted = list(), list()
	# step over the whole set
	for key, desc_list in descriptions.items():
		# generate description
		yhat = generate_desc(model, tokenizer, photos[key], max_length)
		# store actual and predicted
		references = [d.split() for d in desc_list]
		actual.append(references)
		predicted.append(yhat.split())
	# calculate BLEU score
	print('BLEU-1: %f' % corpus_bleu(actual, predicted, weights=(0.3, 0.3, 0.3, 0)))


In [1]:
from numpy import argmax
from pickle import load
from nltk.translate.bleu_score import corpus_bleu
filename1 = df_text + "\\" + "Flickr_8k.testImages.txt"
test_images=load_photos(filename)
test_desc=load_clean("descriptions.txt", test_images)
print('Descriptions: test=%d' % len(test_descriptions))
test_features=load_features(test_images)
print('Photos: test=%d' % len(test_features))
import matplotlib.pyplot as plt
from nltk.translate.bleu_score import corpus_bleu
# map an integer to a word
def word_for_id(integer, tokenizer):
	for word, index in tokenizer.word_index.items():
		if index == integer:
			return word
	return None

# generate a description for an image
def generate_desc(model, tokenizer, photo, max_length):
	# seed the generation process
	in_text = '<start>'
	# iterate over the whole length of the sequence
	for i in range(max_length):
		# integer encode input sequence
		sequence = tokenizer.texts_to_sequences([in_text])[0]
		# pad input
		sequence = pad_sequences([sequence], maxlen=max_length)
		# predict next word
		yhat = model.predict([photo,sequence], verbose=0)
		# convert probability to integer
		yhat = argmax(yhat)
		# map integer to word
		word = word_for_id(yhat, tokenizer)
		# stop if we cannot map the word
		if word is None:
			break
		# append as input for generating the next word
		in_text += ' ' + word
		# stop if we predict the end of the sequence
		if word == '<end>':
			break
	return in_text
# Load the model and tokenizer
model = load_model('models/model_9.h5')
tokenizer = load(open('tokenizer.pkl', 'rb'))

# Initialize lists for actual and predicted captions
actual, predicted = list(), list()

# Initialize a list to store the BLEU scores
bleu_scores = []

# Iterate over the test set and generate captions
for img_id, img_features in list(test_desc.items())[:40]:
    yhat = generate_desc(model, tokenizer, test_features[img_id],max_length)
    references = [d.split() for d in img_features]
    actual.append(references)
    predicted.append(yhat.split())
    
    # Calculate the BLEU-1 score and store it in the list
    bleu1 = corpus_bleu(actual, predicted, weights=(0.45, 0, 0, 0))
    bleu_scores.append(bleu1)

# Plot the BLEU scores as a line graph
plt.plot(bleu_scores)
plt.xlabel('Image')
plt.ylabel('BLEU-1 Score')
plt.show()


NameError: name 'load_model' is not defined

In [ ]:
def load_photos(filename):
    file = load_doc(filename)
    images = file.split("\n")[:-1]
    return images

In [71]:
filename1 = df_text + "\\" + "Flickr_8k.testImages.txt"
test_images=load_photos(filename)
test_desc=load_clean("descriptions.txt", test_images)
print('Descriptions: test=%d' % len(test_descriptions))
test_features=load_features(test_images)
print('Photos: test=%d' % len(test_features))
 

Descriptions: test=1000
Photos: test=6000


In [45]:
!pip install nltk

In [46]:
from numpy import argmax
from pickle import load
from nltk.translate.bleu_score import corpus_bleu

In [70]:
test_features.items()

dict_items([('2513260012_03d33305cf.jpg', array([[0.        , 0.13564937, 0.        , ..., 0.33939147, 0.        ,
        0.03670813]], dtype=float32)), ('2903617548_d3e38d7f88.jpg', array([[0.11592605, 0.03276933, 0.09128328, ..., 0.11857748, 0.32035083,
        0.01140824]], dtype=float32)), ('3338291921_fe7ae0c8f8.jpg', array([[0.2573096 , 0.        , 0.        , ..., 0.00151269, 0.03060997,
        0.        ]], dtype=float32)), ('488416045_1c6d903fe0.jpg', array([[0.49020347, 0.00798095, 0.03335606, ..., 0.00099491, 0.        ,
        0.        ]], dtype=float32)), ('2644326817_8f45080b87.jpg', array([[0.01606075, 0.05775176, 0.16788492, ..., 0.09669015, 0.11133684,
        0.09311989]], dtype=float32)), ('218342358_1755a9cce1.jpg', array([[0.03871689, 0.        , 0.0437692 , ..., 0.41199794, 0.12132203,
        0.0241018 ]], dtype=float32)), ('2501968935_02f2cd8079.jpg', array([[0.1482211 , 0.01591403, 0.31501496, ..., 0.14830664, 0.067004  ,
        0.16957058]], dtype=float32

In [47]:
model = load_model('models/model_9.h5')
# evaluate model
evaluate_model(model, test_desc, test_features, tokenizer, max_length)

KeyboardInterrupt: 

In [61]:
import nltk
from nltk.translate.bleu_score import sentence_bleu

# reference caption(s)
ref_captions = [["a person standing on a snowy mountain"], ["a man climbing a hilltop"],['man climbing up a mountain'],['a person is on top on a snomy hill']]

# generated caption
gen_caption = "man climbing up a snowy mountain"

# convert reference captions and generated caption to lists of tokens
ref_captions_tok = [tuple(nltk.word_tokenize(caption.lower())) for ref_captions_i in ref_captions for caption in ref_captions_i]
gen_caption_tok = nltk.word_tokenize(gen_caption.lower())

# calculate BLEU score
bleu_score = sentence_bleu(ref_captions_tok, gen_caption_tok)

print(bleu_score)

0.7071067811865475
